# TP3

**1 - Obtener una detección del logo en cada imagen sin falsos positivos**

In [264]:
import numpy as np
import cv2 as cv
import matplotlib.pyplot as plt # pip install PyQt5
%matplotlib qt

In [13]:
def getMatches(img_rgb, template,isMulti):
    # Los 6 métodos posibles para comparación:
    #methods = ['cv.TM_CCOEFF', 'cv.TM_CCOEFF_NORMED', 'cv.TM_CCORR',
    #       'cv.TM_CCORR_NORMED', 'cv.TM_SQDIFF', 'cv.TM_SQDIFF_NORMED']

    methods = ['cv.TM_CCOEFF']
    rectangle_color = (0, 255, 0)
    template = cv.cvtColor(template, cv.COLOR_RGB2GRAY)
    template = cv.bitwise_not(template)
    img_gray = cv.cvtColor(img_rgb, cv.COLOR_RGB2GRAY)
    for meth in methods:
        # Hago una copia de la imagen porque ciclo a ciclo le dibujo rectángulos
        img_salida = img_rgb.copy()
        method = eval(meth)
        w, h = template.shape[::-1]
        if isMulti == False:
            # Aplicamos la coincidencia de patrones
            #--------------------------------------
            res = cv.matchTemplate(img_gray, template, method)
            #print("% de confianza del matching",res)
            

            min_val, max_val, min_loc, max_loc = cv.minMaxLoc(res)

            # Si el método es TM_SQDIFF o TM_SQDIFF_NORMED, tomamos el mínimo
            if method in [cv.TM_SQDIFF, cv.TM_SQDIFF_NORMED]:
                top_left = min_loc
            else:
                top_left = max_loc

            # Marcamos el lugar donde lo haya encontrado
            #----------------------------------------
            bottom_right = (top_left[0] + w, top_left[1] + h)
            cv.rectangle(img_salida,top_left, bottom_right, rectangle_color, 2)

            # Graficamos el procesamiento y la salida
            #----------------------------------------
            
            plt.figure()
            plt.subplot(121),plt.imshow(res,cmap = 'gray')
            plt.title('Matching Result'), plt.xticks([]), plt.yticks([])
            plt.subplot(122),plt.imshow(img_salida)
            plt.title('Detected Point'), plt.xticks([]), plt.yticks([])
            plt.suptitle(meth)
            plt.show()
        else:
            res = cv.matchTemplate(img_gray,template,cv.TM_CCORR_NORMED)
            # Fijamos un umbral de "coincidencia"
            threshold = 0.64
            loc = np.where( res >= threshold)
            for pt in zip(*loc[::-1]):
                cv.rectangle(img_salida, pt, (pt[0] + w, pt[1] + h), rectangle_color, 2)

            # Graficamos el procesamiento y la salida
            #----------------------------------------
            plt.figure()
            plt.subplot(121),plt.imshow(res,cmap = 'gray')
            plt.title('Matching Result'), plt.xticks([]), plt.yticks([])
            plt.subplot(122),plt.imshow(img_salida)
            plt.title('Detected Point'), plt.xticks([]), plt.yticks([])
            plt.suptitle("Multi")
            plt.show() 

In [265]:
def getMatches2(img_rgb):
    img_rgb= cv.cvtColor(img_rgb, cv.COLOR_BGR2RGB)

    img_gray = cv.cvtColor(img_rgb, cv.COLOR_RGB2GRAY)

    template = cv.imread('./template/pattern.png')
    template = cv.cvtColor(template, cv.COLOR_BGR2GRAY)
    template = cv.bitwise_not(template)

    rectangle_color = (0, 255, 0)  

    factors = [0.25,0.3,0.4,0.5,1.2]

    factors = list(map(float, factors))

    method="cv.TM_CCOEFF"

    # template = cv.pyrDown(template)

    # Hago una copia de la imagen porque ciclo a ciclo le dibujo rectángulos
    img_salida = img_rgb.copy()       
    method = eval("cv.TM_CCOEFF")
    maxScore = 0
    maxW = 0
    maxH = 0
    for templateScale_factor in factors:
        try:
            resicedTemplate = cv.resize(template, None, fx=templateScale_factor, fy=templateScale_factor, interpolation=cv.INTER_LINEAR)
            w, h = resicedTemplate.shape[::-1]
            res = cv.matchTemplate(img_gray,resicedTemplate,method)
            loc = np.where(res >= 0.9)
            for pt in zip(*loc[::-1]):
                match_score = res[pt[1], pt[0]]
                if pt == (0, 0):
                    maxW=w
                    maxH=h
                    maxScore = match_score
                    maxPT = pt
                else:
                    if maxScore < match_score:
                        maxScore = match_score
                        maxPT = pt
                        maxW = w
                        maxH = h
        except cv.error as e:
            print("Error - Template bigger than target image...")
    top_left = maxPT  # Position of the top-left corner of a match
    cv.rectangle(img_salida, top_left, (top_left[0] + maxW, top_left[1] + maxH), rectangle_color, 2)
    print(f"Match found with accuracy {maxScore:.2f} at position {top_left}")
    # Graficamos el procesamiento y la salida
    #----------------------------------------
    plt.figure()
    plt.subplot(121),plt.imshow(res,cmap = 'gray')
    plt.title('Matching Result'), plt.xticks([]), plt.yticks([])
    plt.subplot(122),plt.imshow(img_salida)
    plt.title('Detected Point'), plt.xticks([]), plt.yticks([])
    plt.suptitle("Multi")
    plt.show()

In [346]:
def getMatches3(img_rgb):
    img_rgb= cv.cvtColor(img_rgb, cv.COLOR_BGR2RGB)
    img_gray = cv.cvtColor(img_rgb, cv.COLOR_RGB2GRAY)
    template = cv.imread('./template/pattern.png')
    template = cv.cvtColor(template, cv.COLOR_BGR2GRAY)
    rectangle_color = (0, 255, 0)  
    factors = [0.25,0.3,0.4,0.5,1.2]
    factors = list(map(float, factors))
    method="cv.TM_CCOEFF"

    # template = cv.pyrDown(template)

    # Hago una copia de la imagen porque ciclo a ciclo le dibujo rectángulos
    img_salida = img_rgb.copy()       
    method = eval("cv.TM_CCOEFF")
    np.set_printoptions(threshold=np.inf)
    for templateScale_factor in factors:
        try:
            resicedTemplate = cv.resize(template, None, fx=templateScale_factor,
                                         fy=templateScale_factor,
                                           interpolation=cv.INTER_LINEAR)
            w, h = resicedTemplate.shape[::-1]
            res = cv.matchTemplate(img_gray,resicedTemplate,method)
            loc = np.where(res >= 0.9)
            # Create a list of matches with their coordinates and match scores
            matches=np.empty((1, 5))
            for pt in zip(*loc[::-1]):
                values_to_append = [pt[0],pt[1],res[pt[1], pt[0]],w,h]
                matches = np.concatenate((matches, [values_to_append]), axis=0)
            print(values_to_append)
            # Sort the matches by match score in descending order
            print("Factor: ",templateScale_factor)
        except cv.error as e:
            print("Error - Template bigger than target image...")
    sorted_indices = np.argsort(matches[:, 2])[::-1]
    sorted_matches = matches[sorted_indices]
    #sorted_matches = sorted(matches, key=lambda x: x[0], reverse=True)
    #print("Sorted matches:", sorted_matches)
    for match in sorted_matches[:5]:
        x, y, match_score ,w ,h = match
        print("Match found with accuracy ",match_score," at position ",(x,y))
        top_left = (x.astype(int), y.astype(int))
        bottom_right = ((x + w).astype(int), (y + h).astype(int))
        cv.rectangle(img_salida, top_left, bottom_right, rectangle_color, 2)
        match_score = sorted_matches[2]
            
    # Graficamos el procesamiento y la salida
    #----------------------------------------
    plt.figure()
    plt.subplot(121),plt.imshow(res,cmap = 'gray')
    plt.title('Matching Result'), plt.xticks([]), plt.yticks([])
    plt.subplot(122),plt.imshow(img_salida)
    plt.title('Detected Point'), plt.xticks([]), plt.yticks([])
    plt.suptitle("Multi")
    plt.show()

In [267]:
def setCanny(img):
    # Cargo la imagen
    #================
    gray = cv.cvtColor(img, cv.COLOR_RGB2GRAY)

    # Aplico Canny
    #=============
    edges = cv.Canny(img, threshold1=5, threshold2=20)

    # Muestro la imagen
    #==================
    #cv.imshow("CannyCV",edges)
    return edges

In [423]:
def getMatchesMulti(img_rgb,isMulti):
    #template = cv.imread('./template/pattern.png')
    #template = setCanny(template)
    #img_gray = setCanny(img_rgb)

    img_rgb= cv.cvtColor(img_rgb, cv.COLOR_BGR2RGB)
    img_gray = cv.cvtColor(img_rgb, cv.COLOR_RGB2GRAY)
    template = cv.imread('./template/pattern.png')
    template = cv.cvtColor(template, cv.COLOR_BGR2GRAY)
    template = cv.bitwise_not(template)
    rectangle_color = (0, 255, 0)  
    factors = [0.25,0.3,0.4,0.5,1.2]
    #factors = [0.25]
    factors = list(map(float, factors))
    meth=""

    # template = cv.pyrDown(template)

    # Hago una copia de la imagen porque ciclo a ciclo le dibujo rectángulos
    img_salida = img_rgb.copy()#cv.cvtColor(img_rgb, cv.COLOR_BGR2RGB)       
    #img_salida = img_gray.copy()
    np.set_printoptions(threshold=np.inf)
    matches=np.empty((1, 5))

    if isMulti:
        meth='cv.TM_CCOEFF_NORMED'
    else:
        meth='cv.TM_CCOEFF'
    method = eval(meth)
    for templateScale_factor in factors:
        try:
            resicedTemplate = cv.resize(template, None, fx=templateScale_factor,
                                        fy=templateScale_factor,
                                        interpolation=cv.INTER_LINEAR)
            w, h = resicedTemplate.shape[::-1]
            res = cv.matchTemplate(img_gray,resicedTemplate,method)
            threshold=0
            if isMulti:
                threshold = 0.20
            else:
                threshold = 26000000
            loc = np.where(res>=threshold)
            # Create a list of matches with their coordinates and match scores
            x=0
            for pt in zip(*loc[::-1]):
                matchScore=res[pt[1], pt[0]]
                values_to_append = [pt[0],pt[1],matchScore,w,h]
                matches = np.concatenate((matches, [values_to_append]), axis=0)
                x=1;
                #print("Match Score:",matchScore,"(",pt[0],",",pt[1],")")
            if x==1:
                print("Method:",meth,"Factor: ",templateScale_factor,"tp shape:(",w,",",h,")")
            else:
                print("Error - No values to append in this factor value...",templateScale_factor)
        except cv.error as e:
            print("Error - Template bigger than target image...")
    # Sort the matches by match score in descending order
    sorted_indices = np.argsort(matches[:, 2])[::-1]
    sorted_matches = matches[sorted_indices]
    #sorted_matches = sorted(matches, key=lambda x: x[0], reverse=True)
    #print("Sorted matches:", sorted_matches)
    for match in sorted_matches[:6]:
        x, y, match_score ,w ,h = match
        if isMulti and match_score < 1:
            print("Match found with accuracy ",match_score," at position ",(x,y)," with tp shape (",w,",",h,")")
            top_left = (x.astype(int), y.astype(int))
            bottom_right = ((x + w).astype(int), (y + h).astype(int))
            cv.rectangle(img_salida, top_left, bottom_right, rectangle_color, 2)
        #match_score = sorted_matches[2]
    # Graficamos el procesamiento y la salida
    #----------------------------------------
    plt.figure()
    plt.subplot(121),plt.imshow(res,cmap = 'gray')
    plt.title('Matching Result'), plt.xticks([]), plt.yticks([])
    plt.subplot(122),plt.imshow(img_salida)
    plt.title('Detected Point'), plt.xticks([]), plt.yticks([])
    plt.suptitle("Multi")
    plt.show()

In [311]:
def resizeImgAndTemplate(img,templateScale_factor):
    img_rgb= cv.cvtColor(img, cv.COLOR_BGR2RGB)
    template = cv.imread('./template/pattern.png')
    template = cv.cvtColor(template, cv.COLOR_BGR2RGB)

    # template = cv.pyrDown(template)
    template = cv.resize(template, None, fx=templateScale_factor, fy=templateScale_factor, interpolation=cv.INTER_LINEAR)

    return template, img_rgb

coca_logo_1.png - 0.4 - cv.bitwise_not(template) ON
coca_logo_2.png - 0.5 - cv.bitwise_not(template) ON
coca_retro_1.png - 1.2 - cv.bitwise_not(template) OFF
coca_retro_2.png - 0.4 - cv.bitwise_not(template) ON

In [312]:
img = cv.imread('./images/coca_logo_1.png')
template, img = resizeImgAndTemplate(img,0.4)
plt.figure()
plt.subplot(1,2,1)
plt.imshow(template)
plt.subplot(1,2,2)
plt.imshow(img)

In [394]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_logo_1.png')
template, img = resizeImgAndTemplate(img,0.3)
getMatches(img, template, False)

In [421]:
# Cargamos la imagen a procesar
img = cv.imread('./images/COCA-COLA-LOGO.jpg')
#template, img = resizeImgAndTemplate(img,1,0.3)
getMatchesMulti(img,False)

Error - No values to append in this factor value... 0.25
Error - No values to append in this factor value... 0.3
Method: cv.TM_CCOEFF Factor:  0.4 tp shape:( 160 , 70 )
Method: cv.TM_CCOEFF Factor:  0.5 tp shape:( 200 , 88 )


KeyboardInterrupt: 

In [429]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_logo_1.png')
#template, img = resizeImgAndTemplate(img,1,0.3)
getMatches2(img)

Error - Template bigger than target image...
Match found with accuracy 14581879.00 at position (33, 200)


In [430]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_logo_2.png')
getMatches2(img)

Error - Template bigger than target image...
Match found with accuracy 10251771.00 at position (0, 129)


In [432]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_retro_1.png')
#img=cv.bitwise_not(img)
#template, img = resizeImgAndTemplate(img,1.2)
getMatches2(img)

Match found with accuracy 115224496.00 at position (6, 0)


In [434]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_retro_2.png')
#template, img = resizeImgAndTemplate(img,1,0.4)
getMatches3(img)

[575, 385, 87328.62, 100, 44]
Factor:  0.25
[166, 376, 29311.193, 120, 52]
Factor:  0.3
[6, 352, 34916.152, 160, 70]
Factor:  0.4
[364, 332, 63707.42, 200, 88]
Factor:  0.5
[235, 219, 4071954.8, 480, 210]
Factor:  1.2
Match found with accuracy  64614616.0  at position  (110.0, 201.0)
Match found with accuracy  64545012.0  at position  (109.0, 201.0)
Match found with accuracy  64534380.0  at position  (111.0, 201.0)
Match found with accuracy  64497532.0  at position  (110.0, 202.0)
Match found with accuracy  64429136.0  at position  (109.0, 202.0)


In [ ]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_multi.png')
template, img = resizeImgAndTemplate(img,0.25)
getMatches(img,template,True)


**2 - Plantear y validar un algoritmo para múltiples detecciones en la imagen
coca_multi.png con el mismo témplate del ítem 1**

In [412]:
# Cargamos la imagen a procesar
img = cv.imread('./images/coca_multi.png')
#template, img = resizeImgAndTemplate(img,1,0.25)
getMatchesMulti(img,True)

Match Score: 0.20078157 ( 371 , 58 )
Match Score: 0.20187531 ( 372 , 58 )
Match Score: 0.20496851 ( 373 , 58 )
Match Score: 0.20398559 ( 374 , 58 )
Match Score: 0.2079871 ( 244 , 59 )
Match Score: 0.20291795 ( 245 , 59 )
Match Score: 0.21427014 ( 368 , 59 )
Match Score: 0.22282755 ( 369 , 59 )
Match Score: 0.22304578 ( 370 , 59 )
Match Score: 0.2254889 ( 371 , 59 )
Match Score: 0.22814804 ( 372 , 59 )
Match Score: 0.23110487 ( 373 , 59 )
Match Score: 0.22577435 ( 374 , 59 )
Match Score: 0.2214844 ( 375 , 59 )
Match Score: 0.21218476 ( 376 , 59 )
Match Score: 0.20545794 ( 377 , 59 )
Match Score: 0.20628512 ( 378 , 59 )
Match Score: 0.21321799 ( 379 , 59 )
Match Score: 0.2139176 ( 380 , 59 )
Match Score: 0.20641416 ( 381 , 59 )
Match Score: 0.21068536 ( 241 , 60 )
Match Score: 0.230449 ( 242 , 60 )
Match Score: 0.24266113 ( 243 , 60 )
Match Score: 0.24582887 ( 244 , 60 )
Match Score: 0.23514122 ( 245 , 60 )
Match Score: 0.22298372 ( 246 , 60 )
Match Score: 0.21365932 ( 247 , 60 )
Match S